# 01_GriddedDiagnostics_TempAdvection_ERA5

## In this notebook, we'll cover the following:
1. Select a date and access the ERA5 dataset
2. Subset the desired variables along their dimensions
3. Calculate and visualize diagnostic quantities.
4. Smooth the diagnostic field.

# <span style="color:purple">0) Imports </span>

In [ ]:
import xarray as xr
import pandas as pd
import numpy as np
from datetime import datetime as dt
from metpy.units import units
import metpy.calc as mpcalc
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import matplotlib.pyplot as plt

# <span style="color:purple">1) Specify a starting and ending date/time, regional extent, vertical levels, and access the ERA5</span>

<div class="alert alert-danger">Restrict your date range to no more than 7 days!</div>

In [ ]:
# Areal extent
lonW = -100
lonE = -60
latS = 25
latN = 55
cLat, cLon = (latS + latN)/2, (lonW + lonE)/2

# Recall that in ERA5, longitudes run between 0 and 360, not -180 and 180
if (lonW < 0 ):
    lonW = lonW + 360
if (lonE < 0 ):
    lonE = lonE + 360
    
expand = 1
latRange = np.arange(latS - expand,latN + expand,.25) # expand the data range a bit beyond the plot range
lonRange = np.arange((lonW - expand),(lonE + expand),.25) # Need to match longitude values to those of the coordinate variable

# Vertical level specification
pLevel = 850
levStr = f'{pLevel}'

startYear = 2007
startMonth = 2
startDay = 14
startHour = 12
startMinute = 0
startDateTime = dt(startYear,startMonth,startDay, startHour, startMinute)

endYear = 2007
endMonth = 2
endDay = 14
endHour = 12
endMinute = 0
endDateTime = dt(endYear,endMonth,endDay, endHour, endMinute)

delta_time = endDateTime - startDateTime
time_range_max = 7*86400

if (delta_time.total_seconds() > time_range_max):
        raise RuntimeError("Your time range must not exceed 7 days. Go back and try again.")

<div class="alert alert-warning">The variable names and two of the dimension names in our local 2023-2024 archive differ from those in the Google Cloud Platform-hosted multi-decade archive. In the cell below, we employ a dictionary that translates the former to the latter. We then pass the dictionary to Xarray's <code>rename_dims</code> and <code>rename_vars</code> functions to perform the renamings.
</div>

<div class="alert alert-info"><b>Chunks:</b> See <a href="https://docs.xarray.dev/en/stable/user-guide/dask.html#chunking-and-performance">this link</a> for more info about chunking in Xarray.
</div>

In [ ]:
Wb2EndDate = dt(2023,1,10)
if (endDateTime <= Wb2EndDate):
    ds = xr.open_dataset(
     'gs://weatherbench2/datasets/era5/1959-2023_01_10-wb13-6h-1440x721.zarr', 
     chunks={'time': 48},
     consolidated=True,
     engine='zarr'
)
else: 
    import glob, os
    input_directory = '/free/ktyle/era5'
    files = glob.glob(os.path.join(input_directory,'*.nc'))
    varDict = {'valid_time': 'time', 
               'pressure_level': 'level',
               'msl': 'mean_sea_level_pressure',
               'q': 'specific_humidity',
               't': 'temperature',
               'u': 'u_component_of_wind',
               'v': 'v_component_of_wind',
               'w': 'vertical_velocity',
               'z': 'geopotential'}
    dimDict = {'valid_time': 'time',
               'pressure_level': 'level'}
    ds = xr.open_mfdataset(files).rename_dims(dimDict).rename_vars(varDict)

Examine the `Dataset`

In [ ]:
ds

# <span style="color:purple">2) Specify a date/time range, and subset the desired `Dataset`s along their dimensions.</span>

Create a list of date and times based on what we specified for the initial and final times, using Pandas' date_range function

In [ ]:
dateList = pd.date_range(startDateTime, endDateTime,freq="6h")
dateList

We will display temperature and wind (and ultimately, temperature advection), so pick the relevant variables.

### Now create objects for our desired DataArrays based on the coordinates we have subsetted.

<div class="alert alert-warning"><b>Be patient:</b> If you are reading from the GCP WeatherBench archive, depending on how much data you are subsetting, this next cell, which actually loads the data into memory, may take some time to complete. This and other similar examples in this week's material typically take a minute or so to load.
</div>

In [ ]:
# Data variable selection
T = ds['temperature'].sel(time=dateList,level=pLevel,latitude=latRange,longitude=lonRange).compute()
U = ds['u_component_of_wind'].sel(time=dateList,level=pLevel,latitude=latRange,longitude=lonRange).compute()
V = ds['v_component_of_wind'].sel(time=dateList,level=pLevel,latitude=latRange,longitude=lonRange).compute()

<div class="alert alert-warning"><b>Notice the <i>compute()</i> function:</b> When we open a dataset that is comprised of multiple files, either via the <code>xr.open_mfdataset</code> function or if the data is stored in <a href="https://zarr.readthedocs.io">the Zarr file format</a>, the dataset and its constituent data arrays are in the form of <a href="https://docs.xarray.dev/en/stable/user-guide/dask.html">Dask</a> dataset / data arrays. While a detailed exploration of Dask is beyond the scope of this notebook and course, here we will use Xarray's <code>compute</code> function to read the dataset/array into memory, so that we can later do unit conversions and diagnostics with MetPy.
</div>

In [ ]:
T

# <span style="color:purple">3) Calculate and visualize diagnostic quantities.</span>

Define our subsetted coordinate arrays of lat and lon. Pull them from any of the DataArrays. We'll need to pass these into the contouring functions later on.

In [ ]:
lats = T.latitude
lons = T.longitude

### First, let's just plot contour lines of temperature and wind barbs.

#### Unit conversions
We will create new objects for T, U and V in knots, since we will want to preserve the original units (m/s) when it comes time to calculate temperature advection.

In [ ]:
TCel = T.metpy.convert_units('degC')
UKts = U.metpy.convert_units('kts')
VKts = V.metpy.convert_units('kts')

Create an array of values for the temperature contours: since we are using contour lines, simply define a range large enough to encompass the expected values, and set a contour interval.

In [ ]:
TCel.min().values, TCel.max().values

In [ ]:
cint = 2
minT, maxT = (-30,22)
TContours = np.arange(minT, maxT, cint)

#### Make the map

In [ ]:
constrainLat, constrainLon = (0.5, 4.0)
proj_map = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)
proj_data = ccrs.PlateCarree() # Our data is lat-lon; thus its native projection is Plate Carree.
res = '50m'

Although there is just a single time in our time range, we'll still employ a loop here in case we wanted to include multiple times later on.

In [ ]:
for time in dateList:
    print(f"Processing {time}")
    
    # Create the time strings, for the figure title as well as for the file name.
    timeStr = dt.strftime(time,format="%Y-%m-%d %H%M UTC")
    timeStrFile = dt.strftime(time,format="%Y%m%d%H")

    tl1 = f'ERA5, Valid at: {timeStr}'
    tl2 = f'{levStr} hPa temperature (°C) and wind (kts)'
    
    title_line = f'{tl1}\n{tl2}\n'
    
    fig = plt.figure(figsize=(21,15)) # Increase size to adjust for the constrained lats/lons
    ax = fig.add_subplot(1,1,1,projection=proj_map)
    ax.set_extent ([lonW+constrainLon,lonE-constrainLon,latS+constrainLat,latN-constrainLat])
    ax.add_feature(cfeature.COASTLINE.with_scale(res))
    ax.add_feature(cfeature.STATES.with_scale(res),edgecolor='brown')
    
    # Need to use Xarray's sel method here to specify the current time for any DataArray you are plotting.
    
    # 1. Contour lines of temperature
    cT = ax.contour(lons, lats, TCel.sel(time=time), levels=TContours, colors='orange', linewidths=3, transform=proj_data)
    ax.clabel(cT, inline=1, fontsize=12, fmt='%.0f')
    
    # 4. wind barbs
    # Plotting wind barbs uses the ax.barbs method. Here, you can't pass in the DataArray directly; you can only pass in the array's values.
    # Also need to sample (skip) a selected # of points to keep the plot readable.
    # Remember to use Xarray's sel method here as well to specify the current time.
    skip = 5
    ax.barbs(lons[::skip],lats[::skip],UKts.sel(time=time)[::skip,::skip].values, VKts.sel(time=time)[::skip,::skip].values, color='purple',zorder=2,transform=proj_data)

    title = plt.title(title_line,fontsize=16)
    


#### Look at the map and you should easily be able to identify the areas of prominent warm and cold advection. Instead of qualitatively assessing a diagnostic quantity such as temperature advection, how about we quantify it? For that, we will use MetPy's <i>diagnostic library</i>, which we have imported as `mpcalc`.

## [MetPy Diagnostics](https://unidata.github.io/MetPy/latest/api/generated/metpy.calc.html)

#### Let's explore the `advection` diagnostic: https://unidata.github.io/MetPy/latest/api/generated/metpy.calc.advection.html

#### In order to calculate horizontal tempareture advection, we need a <i>scalar</i> quantity (temperature, the "thing" being advected), and a <i>vector</i> field (wind, the "thing" doing the advecting). 

For MetPy's advection function, we pass in the scalar, followed by the vector ... in this case, T followed by U and V.

In [ ]:
# Calculate temperature advection by the horizontal wind:
tAdv = mpcalc.advection(T, U, V)

Let's look at the output `DataArray`, containing the calculated values (and units) of temperature advection. Note how these values scale ... on the order of 10**-5.

In [ ]:
tAdv

Let's get a quick visualization, using Xarray's built-in interface to Matplotlib.

In [ ]:
tAdv.plot(figsize=(15,10),cmap='coolwarm')

#### We have three strategies to make the resulting map look nicer:
1. Scale up the values by an appropriate power of ten
2. Focus on the more extreme values of temperature advection: thus, do not contour values that are close to zero.
3. Smooth the values of temperature advection ... especially important in datasets with a high degree of horizontal resolution.

Let's take care of the first two strategies, and then assess the need for smoothing.

### Scale these values up by 1e5 (or 1 * 10**5, or 100,000) and find the min/max values. Use these to inform the setting of the contour fill intervals.

In [ ]:
scale = 1e5
minTAdv = (tAdv*scale).min().values
maxTAdv = (tAdv*scale).max().values
print (minTAdv, maxTAdv)

### Usually, we wish to avoid plotting the "zero" contour line for diagnostic quantities such as divergence, advection, and frontogenesis. Thus, create two lists of values ... one for negative and one for positive.

In [ ]:
advInc = 50
negAdvContours = np.arange (-300, 0, advInc)
posAdvContours = np.arange (50, 350, advInc)

In [ ]:
negAdvContours

### Now, let's plot temperature advection on the map. 

In [ ]:
for time in dateList:
    print(f'Processing {time}')
    
    # Create the time strings, for the figure title as well as for the file name.
    timeStr = dt.strftime(time,format="%Y-%m-%d %H%M UTC")
    timeStrFile = dt.strftime(time,format="%Y%m%d%H")
    
    tl1 = f'ERA5, Valid at: {timeStr}'
    tl2 = f'{levStr} hPa temperature advection (°C x 10**5 / s)'
    
    title_line = f'{tl1}\n{tl2}\n'
    
    fig = plt.figure(figsize=(21,15)) # Increase size to adjust for the constrained lats/lons
    ax = fig.add_subplot(1,1,1,projection=proj_map)
    ax.set_extent ([lonW+constrainLon,lonE-constrainLon,latS+constrainLat,latN-constrainLat])
    ax.add_feature(cfeature.COASTLINE.with_scale(res))
    ax.add_feature(cfeature.STATES.with_scale(res),edgecolor='brown')
    
    # Need to use Xarray's sel method here to specify the current time for any DataArray you are plotting.
    
    # 1a. Contour lines of warm (positive temperature) advection.
    # Don't forget to multiply by the scaling factor!
    cPosTAdv = ax.contour(lons, lats, tAdv.sel(time=time)*scale, levels=posAdvContours, colors='red', linewidths=3, transform=proj_data)
    ax.clabel(cPosTAdv, inline=1, fontsize=12, fmt='%.0f')
    
    # 1b. Contour lines of cold (negative temperature) advection
    cNegTAdv = ax.contour(lons, lats, tAdv.sel(time=time)*scale, levels=negAdvContours, colors='blue', linewidths=3, transform=proj_data)
    ax.clabel(cNegTAdv, inline=1, fontsize=12, fmt='%.0f')
    
    title = ax.set_title(title_line,fontsize=16)
    #Generate a string for the file name and save the graphic to your current directory.
    fileName = f'{timeStrFile}_ERA5_{levStr}_TAdv.png'
    fig.savefig(fileName)


# <span style="color:purple">4. Smooth the diagnostic field.</span>

This is not a terribly "noisy" field. But let's demonstrate the technique of employing a smoothing function. We will use a [Gaussian filter](https://docs.scipy.org/doc/scipy/reference/generated/scipy.ndimage.gaussian_filter.html),  from the [SciPy library](https://scipy.org/scipylib/), which, along with NumPy and Pandas, is one of the core packages in Python's scientific software ecosystem.

MetPy now includes the Gaussian smoother as one of its diagnostics.

In [ ]:
sigma = 8.0 # this depends on how noisy your data is, adjust as necessary

tAdvSmooth = mpcalc.smooth_gaussian(tAdv, sigma)

As we did before with the unsmoothed values, let's look at the resulting `DataArray` and its extrema.

In [ ]:
tAdvSmooth

In [ ]:
scale = 1e5
minTAdv = (tAdvSmooth * scale).min().values
maxTAdv = (tAdvSmooth * scale).max().values
print (minTAdv, maxTAdv)

Not surprisingly, the magnitude of the extrema decreased.

Plot the smoothed advection field.

In [ ]:
for time in dateList:
    print(f'Processing {time}')
    
    # Create the time strings, for the figure title as well as for the file name.
    timeStr = dt.strftime(time,format="%Y-%m-%d %H%M UTC")
    timeStrFile = dt.strftime(time,format="%Y%m%d%H")
    
    tl1 = f'ERA5, Valid at: {timeStr}'
    tl2 = f'{levStr} hPa temperature advection (°C x 10**5 / s), smoothed'

    title_line = f'{tl1}\n{tl2}\n'
    
    fig = plt.figure(figsize=(21,15)) # Increase size to adjust for the constrained lats/lons
    ax = fig.add_subplot(1,1,1,projection=proj_map)
    ax.set_extent ([lonW+constrainLon,lonE-constrainLon,latS+constrainLat,latN-constrainLat])
    ax.add_feature(cfeature.COASTLINE.with_scale(res))
    ax.add_feature(cfeature.STATES.with_scale(res),edgecolor='brown')
    
    # Need to use Xarray's sel method here to specify the current time for any DataArray you are plotting.
    
    # 1a. Contour lines of warm (positive temperature) advection.
    # Don't forget to multiply by the scaling factor!
    cPosTAdv = ax.contour(lons, lats, tAdvSmooth.sel(time=time)*scale, levels=posAdvContours, colors='red', linewidths=3, transform=proj_data)
    ax.clabel(cPosTAdv, inline=1, fontsize=12, fmt='%.0f')
    
    # 1b. Contour lines of cold (negative temperature) advection
    cNegTAdv = ax.contour(lons, lats, tAdvSmooth.sel(time=time)*scale, levels=negAdvContours, colors='blue', linewidths=3, transform=proj_data)
    ax.clabel(cNegTAdv, inline=1, fontsize=12, fmt='%.0f')
    
    title = ax.set_title(title_line,fontsize=16)
    #Generate a string for the file name and save the graphic to your current directory.
    fileName = f'{timeStrFile}_ERA5_{levStr}_TAdvSmth.png'
    fig.savefig(fileName)
